# Imports

In [1]:
%%capture
!pip install -U feature-engine

In [2]:
import os
import pandas as pd
import numpy as np
from copy import deepcopy
import category_encoders as ce
from feature_engine.creation import CyclicalTransformer
from pandas_profiling import ProfileReport
import matplotlib.pyplot as plt

from utils import get_target
from features import get_time_features

# Parameters

In [3]:
USE_FULL = True
data_path = 'data'
train_filename = 'training_set_VU_DM.csv'
test_filename = 'test_set_VU_DM.csv'

CAT_FEATURES = ['site_id',
                'visitor_location_country_id',
                'prop_country_id',
                'prop_id',
                'srch_destination_id']

bool_cols = ['prop_brand_bool',
             'promotion_flag',
             'srch_saturday_night_bool',
             'random_bool']

drop_cols = ['position', 'click_bool',
             'gross_bookings_usd', 'booking_bool']

group_col = 'srch_id'
time_col = 'date_time'

# Data reading

In [4]:
if USE_FULL:
    df = pd.read_csv(os.path.join(data_path, train_filename))
else:
    import random
    p = 0.01
    df = pd.read_csv(os.path.join(data_path, train_filename),
                     header=0,
                     skiprows=lambda i: i > 0 and random.random() > p)
df.shape

(4958347, 54)

In [5]:
subm_df = pd.read_csv(os.path.join(data_path, test_filename))
subm_df.shape

(4959183, 50)

In [6]:
# split later. be very careful
df['subm'] = False
subm_df['subm'] = True
df = pd.concat([df, subm_df])

df['date_time'] = pd.to_datetime(df['date_time'])

df.shape

(9917530, 55)

# Missing values

In [ ]:
df['prop_log_historical_price'].replace(0, np.nan, inplace=True)

# Time-independent feature engineering

## Decompose time

In [7]:
%%time

# various time-related columns are added to the df
df = get_time_features(deepcopy(df), 'date_time')

# time column is encoded as some algorithms don't work with datetime. 
# keep both. each specific model may load needed columns
enc = ce.OrdinalEncoder(cols=['date_time'])
df.sort_values(['date_time'], inplace=True)
df = enc.fit_transform(df)
# df.drop('date_time', axis=1, inplace=True)

CPU times: user 4min 52s, sys: 1min 8s, total: 6min
Wall time: 6min 17s


In [8]:
pd.set_option('max_columns', None)
df.head()

srch_id  date_time  site_id  visitor_location_country_id  \
485242    32491          1       24                          216   
485243    32491          1       24                          216   
485244    32491          1       24                          216   
485245    32491          1       24                          216   
485246    32491          1       24                          216   

        visitor_hist_starrating  visitor_hist_adr_usd  prop_country_id  \
485242                      NaN                   NaN              225   
485243                      NaN                   NaN              225   
485244                      NaN                   NaN              225   
485245                      NaN                   NaN              225   
485246                      NaN                   NaN              225   

        prop_id  prop_starrating  prop_review_score  prop_brand_bool  \
485242      327                4                4.5                0   
485243    20797                3                3.0                0   
485244    24202                3                0.0                0   
485245    33813                5                4.5                1   
485246    36599                3                4.0                0   

        prop_location_score1  prop_location_score2  prop_log_historical_price  \
485242                  3.66                0.1358                       5.31   
485243                  4.65                0.1955                       4.97   
485244                  4.73                0.3831                       4.97   
485245                  4.76                0.3524                       6.13   
485246                  4.64                0.3488                       5.13   

        position  price_usd  promotion_flag  srch_destination_id  \
485242       NaN     142.71               0                14083   
485243       NaN      79.22               0                14083   
485244       NaN      93.07               1                14083   
485245       NaN     278.63               0                14083   
485246       NaN     100.92               1                14083   

        srch_length_of_stay  srch_booking_window  srch_adults_count  \
485242                    2                   16                  1   
485243                    2                   16                  1   
485244                    2                   16                  1   
485245                    2                   16                  1   
485246                    2                   16                  1   

        srch_children_count  srch_room_count  srch_saturday_night_bool  \
485242                    0                1                         1   
485243                    0                1                         1   
485244                    0                1                         1   
485245                    0                1                         1   
485246                    0                1                         1   

        srch_query_affinity_score  orig_destination_distance  random_bool  \
485242                        NaN                        NaN            0   
485243                        NaN                        NaN            0   
485244                        NaN                        NaN            0   
485245                        NaN                        NaN            0   
485246                        NaN                        NaN            0   

        comp1_rate  comp1_inv  comp1_rate_percent_diff  comp2_rate  comp2_inv  \
485242         NaN        NaN                      NaN         1.0        0.0   
485243         NaN        NaN                      NaN         NaN        NaN   
485244         NaN        NaN                      NaN         NaN        NaN   
485245         NaN        NaN                      NaN         0.0        0.0   
485246         NaN        NaN                      NaN         1.0        0.0   

   

## Time cyclicals

In [9]:
max_values_dict = {'day': 31,
                   'month': 12,
                   'quarter': 4,
                   'week': 52,
                   'dow': 7,
                   'doy': 366,
                   'season_num': 4}

cyclical = CyclicalTransformer(variables=list(max_values_dict.keys()), 
                               drop_original=False,
                               max_values=max_values_dict)

df = cyclical.fit_transform(df)
df.head()

srch_id  date_time  site_id  visitor_location_country_id  \
485242    32491          1       24                          216   
485243    32491          1       24                          216   
485244    32491          1       24                          216   
485245    32491          1       24                          216   
485246    32491          1       24                          216   

        visitor_hist_starrating  visitor_hist_adr_usd  prop_country_id  \
485242                      NaN                   NaN              225   
485243                      NaN                   NaN              225   
485244                      NaN                   NaN              225   
485245                      NaN                   NaN              225   
485246                      NaN                   NaN              225   

        prop_id  prop_starrating  prop_review_score  prop_brand_bool  \
485242      327                4                4.5                0   
485243    20797                3                3.0                0   
485244    24202                3                0.0                0   
485245    33813                5                4.5                1   
485246    36599                3                4.0                0   

        prop_location_score1  prop_location_score2  prop_log_historical_price  \
485242                  3.66                0.1358                       5.31   
485243                  4.65                0.1955                       4.97   
485244                  4.73                0.3831                       4.97   
485245                  4.76                0.3524                       6.13   
485246                  4.64                0.3488                       5.13   

        position  price_usd  promotion_flag  srch_destination_id  \
485242       NaN     142.71               0                14083   
485243       NaN      79.22               0                14083   
485244       NaN      93.07               1                14083   
485245       NaN     278.63               0                14083   
485246       NaN     100.92               1                14083   

        srch_length_of_stay  srch_booking_window  srch_adults_count  \
485242                    2                   16                  1   
485243                    2                   16                  1   
485244                    2                   16                  1   
485245                    2                   16                  1   
485246                    2                   16                  1   

        srch_children_count  srch_room_count  srch_saturday_night_bool  \
485242                    0                1                         1   
485243                    0                1                         1   
485244                    0                1                         1   
485245                    0                1                         1   
485246                    0                1                         1   

        srch_query_affinity_score  orig_destination_distance  random_bool  \
485242                        NaN                        NaN            0   
485243                        NaN                        NaN            0   
485244                        NaN                        NaN            0   
485245                        NaN                        NaN            0   
485246                        NaN                        NaN            0   

        comp1_rate  comp1_inv  comp1_rate_percent_diff  comp2_rate  comp2_inv  \
485242         NaN        NaN                      NaN         1.0        0.0   
485243         NaN        NaN                      NaN         NaN        NaN   
485244         NaN        NaN                      NaN         NaN        NaN   
485245         NaN        NaN                      NaN         0.0        0.0   
485246         NaN        NaN                      NaN         1.0        0.0   

   

## Competitors

In [10]:
for i in range(1, 9):
    df[f'comp{i}_rate_percent_diff_signed'] = df[f'comp{i}_rate'] * df[f'comp{i}_rate_percent_diff']
    df.drop([f'comp{i}_rate'], axis=1, inplace=True)  # bcs it's just a sign for the new feature

In [11]:
df[sorted([c for c in df.columns if 'comp' in c and 'rate' in c])].head()

comp1_rate_percent_diff  comp1_rate_percent_diff_signed  \
485242                      NaN                             NaN   
485243                      NaN                             NaN   
485244                      NaN                             NaN   
485245                      NaN                             NaN   
485246                      NaN                             NaN   

        comp2_rate_percent_diff  comp2_rate_percent_diff_signed  \
485242                      8.0                             8.0   
485243                      NaN                             NaN   
485244                      NaN                             NaN   
485245                      7.0                             0.0   
485246                      6.0                             6.0   

        comp3_rate_percent_diff  comp3_rate_percent_diff_signed  \
485242                      4.0                             4.0   
485243                      2.0                            -2.0   
485244                      NaN                             NaN   
485245                      3.0                             3.0   
485246                      8.0                             0.0   

        comp4_rate_percent_diff  comp4_rate_percent_diff_signed  \
485242                      4.0                             4.0   
485243                      9.0                             9.0   
485244                      9.0                             9.0   
485245                     15.0                            15.0   
485246                     11.0                            11.0   

        comp5_rate_percent_diff  comp5_rate_percent_diff_signed  \
485242                      7.0                             7.0   
485243                      NaN                             NaN   
485244                      NaN                             NaN   
485245                      7.0                             0.0   
485246                      2.0                             2.0   

        comp6_rate_percent_diff  comp6_rate_percent_diff_signed  \
485242                      NaN                             NaN   
485243                      NaN                             NaN   
485244                      NaN                             NaN   
485245                      NaN                             NaN   
485246                      NaN                             NaN   

        comp7_rate_percent_diff  comp7_rate_percent_diff_signed  \
485242                      NaN                             NaN   
485243                      NaN                             NaN   
485244                      NaN                             NaN   
485245                      NaN                             NaN   
485246                      NaN                             NaN   

        comp8_rate_percent_diff  comp8_rate_percent_diff_signed  
485242                      NaN                             NaN  
485243                      NaN                             NaN  
485244                      NaN                             NaN  
485245                      NaN                             NaN  
485246                      NaN                             NaN

## Money transformations

In [12]:
def num_transformations(df, cols, powers=[0.33, 0.5, 2, 3], log_bases=[2, 10, np.e]):
    for c in cols:
        for p in powers:
            if (p <=2) or (p > 2 and all(df[c] < 100)): 
                df[f'{c}_pow_{p}'] = df[c]**p
        
        for log_base in log_bases:
            df[f'{c}_log_{log_base}'] = np.log(df[c]) / np.log(log_base)
        
        df[c+'_reciprocal'] = 1/(df[c] + 1e-6)
        
        if all(df[c] < 10): 
            df[c+'_exp'] = np.exp(df[c])
    return df

In [13]:
df = num_transformations(df,
                         ['price_usd', 'visitor_hist_adr_usd',
                          'prop_log_historical_price'],
                         powers=[0.33, 0.5, 2, 3],
                         log_bases=[2, 10, round(np.e, 2)])

/Users/Oleg_Litvinov1/opt/anaconda3/lib/python3.8/site-packages/pandas/core/arraylike.py:358: RuntimeWarning: divide by zero encountered in log
  result = getattr(ufunc, method)(*inputs, **kwargs)
/Users/Oleg_Litvinov1/opt/anaconda3/lib/python3.8/site-packages/pandas/core/arraylike.py:358: RuntimeWarning: divide by zero encountered in log
  result = getattr(ufunc, method)(*inputs, **kwargs)
/Users/Oleg_Litvinov1/opt/anaconda3/lib/python3.8/site-packages/pandas/core/arraylike.py:358: RuntimeWarning: divide by zero encountered in log
  result = getattr(ufunc, method)(*inputs, **kwargs)


In [ ]:
df = num_transformations(df,
                         [f'comp{i}_rate_percent_diff' if i in range(1, 9)],
                         powers=[],
                         log_bases=[2, 10])

##

**visitor_hist_adr_usd** - The mean price per night (in US$) of the hotels the customer has previously purchased; null signifies there is no purchase history on the customer  

**price_usd** - Displayed price of the hotel for the given search.  Note that different countries have different conventions regarding displaying taxes and fees and the value may be per night or for the whole stay

In [14]:
df['price_diff_to_usr_hist'] = df['price_usd'] - df['visitor_hist_adr_usd']
df['price_ratio_to_usr_hist'] = df['price_usd'] / df['visitor_hist_adr_usd']

**prop_log_historical_price** - The logarithm of the mean price of the hotel over the last trading period. A 0 will occur if the hotel was not sold in that period.  

In [15]:
df['price_diff_to_place_hist_price'] = df['price_usd'] - np.exp(df['prop_log_historical_price'])
df['place_hist_price_diff_usr_hist'] = np.exp(df['prop_log_historical_price']) - df['visitor_hist_adr_usd']

**gross_booking_usd** - Total value of the transaction.  This can differ from the price_usd due to taxes, fees, conventions on multiple day bookings and purchase of a room type other than the one shown in the search
ID of the destination where the hotel search was performed

In [16]:
df.head(2)

srch_id  date_time  site_id  visitor_location_country_id  \
485242    32491          1       24                          216   
485243    32491          1       24                          216   

        visitor_hist_starrating  visitor_hist_adr_usd  prop_country_id  \
485242                      NaN                   NaN              225   
485243                      NaN                   NaN              225   

        prop_id  prop_starrating  prop_review_score  prop_brand_bool  \
485242      327                4                4.5                0   
485243    20797                3                3.0                0   

        prop_location_score1  prop_location_score2  prop_log_historical_price  \
485242                  3.66                0.1358                       5.31   
485243                  4.65                0.1955                       4.97   

        position  price_usd  promotion_flag  srch_destination_id  \
485242       NaN     142.71               0                14083   
485243       NaN      79.22               0                14083   

        srch_length_of_stay  srch_booking_window  srch_adults_count  \
485242                    2                   16                  1   
485243                    2                   16                  1   

        srch_children_count  srch_room_count  srch_saturday_night_bool  \
485242                    0                1                         1   
485243                    0                1                         1   

        srch_query_affinity_score  orig_destination_distance  random_bool  \
485242                        NaN                        NaN            0   
485243                        NaN                        NaN            0   

        comp1_inv  comp1_rate_percent_diff  comp2_inv  \
485242        NaN                      NaN        0.0   
485243        NaN                      NaN        NaN   

        comp2_rate_percent_diff  comp3_inv  comp3_rate_percent_diff  \
485242                      8.0        0.0                      4.0   
485243                      NaN        0.0                      2.0   

        comp4_inv  comp4_rate_percent_diff  comp5_inv  \
485242        0.0                      4.0        0.0   
485243        0.0                      9.0        0.0   

        comp5_rate_percent_diff  comp6_inv  comp6_rate_percent_diff  \
485242                      7.0        NaN                      NaN   
485243                      NaN        NaN                      NaN   

        comp7_inv  comp7_rate_percent_diff  comp8_inv  \
485242        NaN                      NaN        NaN   
485243        NaN                      NaN        NaN   

        comp8_rate_percent_diff  click_bool  gross_bookings_usd  booking_bool  \
485242                      NaN         NaN                 NaN           NaN   
485243                      NaN         NaN                 NaN           NaN   

        subm  day  month  year  quarter  week  dow  doy  days_in_month  \
485242  True    1     11  2012        4    44    4  306             30   
485243  True    1     11  2012        4    44    4  306             30   

        is_weekend  is_month_start  is_month_end  is_quarter_start  \
485242           0               1             0                 0   
485243           0               1             0                 0   

        is_quarter_end  is_year_start  is_year_end  week_id  season_num  \
485242               0              0            0   201244           4   
485243               0              0            0   201244           4   

        week_summer_index   day_sin  day_cos  month_sin  month_cos  \
485242                 10  0.201299  0.97953       -0.5   0.866025   
485243                 10  0.201299  0.97953       -0.5   0.866025   

         quarter_sin  quarter_cos  week_sin  week_cos   dow_sin   dow_cos  \
485242 -2.449294e-16          1.0 -0.822984  0.568065 -0.433884 -0.900969   
485243 -2.449294e-16          1.

In [17]:
df['usr_extra_pay'] = df['gross_bookings_usd'] - df['price_usd']

## Days of staying

**srch_length_of_stay** - Number of nights stay that was searched


**srch_booking_window** - Number of days in the future the hotel stay started from the search date

In [18]:
df['booking_weeks_ahead'] = df['srch_booking_window'] / 7
df['booking_months_ahead'] = df['srch_booking_window'] / 30

df['len_of_stay_to_booking_ahead_ratio'] = df['srch_booking_window'] / df['srch_length_of_stay']
df['len_of_stay_to_booking_ahead_diff'] = df['srch_booking_window'] - df['srch_length_of_stay']

## Family

**srch_adults_count** - The number of adults specified in the hotel room

 
**srch_children_count** - The number of (extra occupancy) children specified in the hotel room

 
**srch_room_count** - Number of hotel rooms specified in the search

In [19]:
df['children_per_adult'] = df['srch_children_count'] / df['srch_adults_count']
df['total_people'] = df['srch_children_count'] + df['srch_adults_count']
df['people_per_room'] = df['total_people'] / df['srch_room_count']

## Others

**srch_query_affinity_score** - The log of the probability a hotel will be clicked on in Internet searches (hence the values are negative)  A null signifies there are no data (i.e. hotel did not register in any searches)

In [20]:
df['srch_query_affinity_score_prob'] = np.exp(df['srch_query_affinity_score'])

# Data split

In [21]:
df.shape

(9917530, 123)

In [22]:
df.sort_values([group_col, time_col], inplace=True)

In [23]:
# further all feature engineering will be separate

subm_df = deepcopy(df[df['subm'] == True])
df = deepcopy(df[df['subm'] == False])

subm_df.drop(['subm'], axis=1, inplace=True)
df.drop(['subm'], axis=1, inplace=True)

df.shape, subm_df.shape

((4958347, 122), (4959183, 122))

In [24]:
from utils import train_test_group_split, get_target

X = df.drop(drop_cols, axis=1)
y = df.apply(get_target, axis=1)
groups = X[group_col]


X_train_val, X_test, y_train_val, y_test, groups_train_val, groups_test = train_test_group_split(X, y, groups,
                                                                                                 group_array=groups,
                                                                                                 train_size=0.9)
# del X, y

X_train, X_val, y_train, y_val, groups_train, groups_val = train_test_group_split(X_train_val,
                                                                                  y_train_val,
                                                                                  groups_train_val,
                                                                                  group_array=groups_train_val,
                                                                                  train_size=0.9)

In [25]:
# make sure that this is empty
set(X_train[group_col]).intersection(set(X_test[group_col]))

set()

In [26]:
X_train.shape, X_val.shape, X_test.shape

((4016262, 118), (446248, 118), (495837, 118))

# Feature engineering with respect to the time 

# Correlations

In [27]:
profile = ProfileReport(X_train, title="Pandas Profiling Report", minimal=True)
profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [29]:
profile = ProfileReport(X_train.sample(1000), title="Pandas Profiling Report")
profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

# Save tables

In [28]:
X_train.to_csv(os.path.join(data_path, 'X_train.csv'), index=False)
y_train.to_csv(os.path.join(data_path, 'y_train.csv'), index=False)
groups_train.to_csv(os.path.join(data_path, 'groups_train.csv'), index=False)
print('train is done')

X_val.to_csv(os.path.join(data_path, 'X_val.csv'), index=False)
y_val.to_csv(os.path.join(data_path, 'y_val.csv'), index=False)
groups_val.to_csv(os.path.join(data_path, 'groups_val.csv'), index=False)
print('val is done')

X_test.to_csv(os.path.join(data_path, 'X_test.csv'), index=False)
y_test.to_csv(os.path.join(data_path, 'y_test.csv'), index=False)
groups_test.to_csv(os.path.join(data_path, 'groups_test.csv'), index=False)
print('test is done')

subm_df.to_csv(os.path.join(data_path, 'submission_df_preprocessed.csv'), index=False)
print('submission is done')

train is done
val is done
test is done
submission is done
